In [1]:
# Importing libraries
from PIL import Image
from PIL import ImageEnhance
from os.path import expanduser
from os import getcwd

import numpy as np
import scipy.ndimage as ndi
import pandas as pd
import matplotlib.image as mpimg
import plotly.express as px

# Importing specific functions
from skimage.morphology import remove_small_objects, remove_small_holes
from skimage.feature import corner_peaks
from skimage.segmentation import relabel_sequential, watershed
from skimage.measure import regionprops
from skimage.color import label2rgb

# Importing imageMKS_custom functions
from imagemks_custom.filters.fftgaussian import fftgauss
from imagemks_custom.filters.fftedges import local_avg
from imagemks_custom.filters.morphological import smooth_binary
from imagemks_custom.structures.shapes import circle, donut
from imagemks_custom.masking.fourier import maskfourier
from imagemks_custom.visualization.borders import make_boundary_image
from imagemks_custom.workflows.fluorescentcells import segment_fluor_cells, default_parameters

In [2]:
def vis(img, title=None, imgsize=(640, 512), mode='gray'):
    fig = px.imshow(img, title=title, color_continuous_scale='gray')
    fig.update_layout(autosize=False, width=imgsize[0], height=imgsize[1],)
    fig.show()

def labelvis(A, L, bg_color='b', engine='matplotlib'):
    bg_color_code = {
        'b': (0.1,0.1,0.5),
        'g': (0.1,0.5,0.1),
    }
        
    A = label2rgb(L, A, bg_label=0, bg_color=bg_color_code[bg_color], alpha=0.1, image_alpha=1)

    A = np.interp(A, (0,1), (0,255)).astype(np.uint8)

    A = make_boundary_image(L, A)
    
    vis(A, title='Labeled cells', mode='rgb')

In [3]:
imgNum = 5
zoomLev = 2

p = {'smooth_size': 3,
    'intensity_curve': 2,
    'short_th_radius': 50,
    'long_th_radius': 600,
    'min_frequency_to_remove': 1,
    'max_frequency_to_remove': 500,
    'max_size_of_small_objects_to_remove': 300,
    'power_adjust': 1,
    'peak_min_distance': 10,
    'size_after_watershed_to_remove': 300,
    'cyto_local_avg_size': 200,
}

smooth_size = p['smooth_size']
intensity_curve=p['intensity_curve']
short_th_radius=p['short_th_radius']
long_th_radius=p['long_th_radius']
min_frequency_to_remove=p['min_frequency_to_remove']
max_frequency_to_remove=p['max_frequency_to_remove']
max_size_of_small_objects_to_remove=p['max_size_of_small_objects_to_remove']
power_adjust=p['power_adjust']
peak_min_distance=p['peak_min_distance']
size_after_watershed_to_remove=p['size_after_watershed_to_remove']
cyto_local_avg_size=p['cyto_local_avg_size']

# ImageMKS - Loading Data

In [4]:
%cd ../..

/Users/cusniwtt/Documents/GitHub/Automatic-cell-counting-in-immunofluorescence-tissue


In [5]:
dataset = 'Dataset/Sample6x6/'
file_name = '1H_Nrf2_No_ADT_5_DAPI_2_1.png'

Ni = mpimg.imread(dataset+file_name)
vis(Ni, title='Original Image')
#cyto_loader = rwformat(readPath, prefix='g', ftype='.tif')

#Ci = cyto_loader[imgNum]

Ni = np.sum(np.array(Ni), axis=2)
Ni = ( (( Ni-np.amin(Ni)) / np.ptp(Ni)) )

#Ci = np.sum(np.array(Ci), axis=2)
#Ci = ( (( Ci-np.amin(Ci)) / np.ptp(Ci)) )

# Step 1: smoothing intensity values and smoothing out peaks
Ni = fftgauss(Ni, smooth_size, pad_type='edge')

# Step 2: contrast enhancement by scaling intensities (from 0-1) on a curve
########  many other methods can be implemented for this step which could benefit the segmentation
Ni = np.power(Ni/np.amax(Ni), intensity_curve)

In [6]:
vis(Ni, title='Smooting Image')
la = local_avg(Ni, short_th_radius)
vis(la, title='Local Average')

In [7]:
# Step 3: short range local avg threshold
th_short = Ni > local_avg(Ni, short_th_radius)

vis(th_short, title='short range local avg threshold')

# Step 4: long range local avg threshold
th_long = Ni > local_avg(Ni, long_th_radius)

vis(th_long, title='long range local avg threshold')

# Step 5: long && short
th_Ni = (th_short*th_long)

# ImageMKS - Remove Small Objects

In [8]:
# Step 8: remove small objects
th_Ni = remove_small_objects(th_Ni, 20)
th_Ni = remove_small_objects(th_Ni, max_size_of_small_objects_to_remove * (zoomLev))
vis(th_Ni, title='remove small objects')

# ImageMKS - Nucleus Watershed

In [9]:
# Step 9: distance transform
distance = ndi.distance_transform_edt(th_Ni)

# Step 10: mark the maxima in the distance transform and assign labels
peak_markers = corner_peaks(distance, min_distance=peak_min_distance, indices=False)
peak_markers = ndi.label(peak_markers)[0]

# Step 11: separate touching nuclei using the watershed markers
label_Ni = watershed(th_Ni, peak_markers, mask=th_Ni)

# Step 12: removing small regions after the watershed segmenation
label_Ni = remove_small_objects(label_Ni, size_after_watershed_to_remove * (zoomLev))

# Step 13: reassigning labels, so that they are continuously numbered
old_labels = np.unique(label_Ni)
for i in range(len(old_labels)):
    label_Ni[label_Ni == old_labels[i]] = i

labelvis(Ni, label_Ni)